In [294]:
import numpy as np
import matplotlib.pyplot as plt
%matplotlib qt

In [295]:
# Initializes the state to an (n x n) grid with (food) food
def init(n, food):
    grid = np.zeros((n, n))
    
    # Initialize food
    food_loc = np.round(np.random.rand(2, food) * (n - 4)) + 2 
    for i in range(food_loc.shape[1]):
        grid[int(food_loc[0, i]), int(food_loc[1, i])] = -1
        
    # Initialize organisms    
    initial_state = np.linspace(1, n - 1, ((n - 1) // 2) + 1)
    zero = np.zeros(len(initial_state))
    org_loc = np.array([np.append(zero, np.ones(len(zero)) * (n-1)), np.append(initial_state, initial_state)])
    for i in range(org_loc.shape[1]):
        grid[int(org_loc[1][i]), int(org_loc[0][i])] = 1
        
    return grid, food_loc, org_loc

In [296]:
# Checks if the organism can move (not surrounded)
def avaialble(i, j, grid):
    if (i < n - 1 and grid[int(i + 1), int(j)] != 1):
        return True
    elif (i > 0 and grid[int(i - 1), int(j)] != 1):
        return True
    elif (j < n - 1 and grid[int(i), int(j + 1)] != 1):
        return True
    elif (j > 0 and grid[int(i), int(j - 1)] != 1):
        return True
    return False

In [297]:
# Returns the adjacent tile to (i, j) which is closest to a source of food
def closest(i, j, locs, grid):
    x = i
    y = j
    dist = n*n
    
    for k in range(len(locs[0])): # find closest food
        if (np.sqrt((locs[0, k] - i) ** 2 + (locs[1, k] - j) ** 2) < dist):
            dist = np.sqrt((locs[0, k] - i) ** 2 + (locs[1, k] - j) ** 2)
            x = locs[0, k]
            y = locs[1, k]      
    curr_x = i
    curr_y = j
    if x != i or y != j:
        if (i < n - 1 and grid[int(i + 1), int(j)] != 1 and (np.sqrt((x - (i + 1)) ** 2 + ((y - j)) ** 2) < dist)):
            curr_x = i + 1
            curr_y = j
            dist = np.sqrt((x - (i + 1)) ** 2 + ((y - j)) ** 2)
        if (i > 0 and grid[int(i - 1), int(j)] != 1 and (np.sqrt((x - (i - 1)) ** 2 + ((y - j)) ** 2) < dist)):
            curr_x = i - 1
            curr_y = j
            dist = np.sqrt((x - (i - 1)) ** 2 + ((y - j)) ** 2)
        if (j < n - 1 and grid[int(i), int(j + 1)] != 1 and (np.sqrt((x - i) ** 2 + (y - (j + 1)) ** 2) < dist)):
            curr_x = i
            curr_y = j + 1
            dist = np.sqrt((x - i) ** 2 + (y - (j + 1)) ** 2)
        if (j > 0 and grid[int(i), int(j - 1)] != 1 and (np.sqrt((x - i) ** 2 + (y - (j - 1)) ** 2) < dist)):
            curr_x = i
            curr_y = j - 1 
            dist = np.sqrt((x - i) ** 2 + (y - (j - 1)) ** 2)
    return curr_x, curr_y        

In [298]:
# Returns the number of empty spots in the grid
def spaces_left(grid, lower, upper):
    return ((upper - lower)**2) - np.count_nonzero(grid) 

In [299]:
def getImage(path):
    return OffsetImage(plt.imread(path, format="jpg"), zoom=.02)

In [329]:
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Final', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=4, metadata=metadata,bitrate=200000)
fig, axis = plt.subplots(1, 2, figsize=(12.4,6.4))
box = axis[0].get_position()
axis[0].set_position([box.x0, box.y0, box.width * 0.8, box.height])

box = axis[1].get_position()
axis[1].set_position([box.x0, box.y0 + box.height * 0.1,
                 box.width, box.height * 0.9])

paths = ['nugget.jpg']

n = 30
food_count = 15
grid, food_loc, org_loc = init(n, food_count)

with writer.saving(fig, "animation1.mp4", dpi=200):
    iterations = 80
    active = np.copy(org_loc)
    active_food = np.copy(food_loc)
    sizes = np.ones(len(active[0]))        # current sizes
    speeds = np.ones(len(active[0]))       # current speeds
    consumption = np.zeros(len(active[0])) # current consumption
    energy = np.ones(len(active[0])) * 15
    for i in range(iterations):
        curr_x = np.array([]) # x pos of current organisms
        curr_y = np.array([]) # y pos of current organisms
        ate_x = np.array([])  # x pos of evolving organisms
        ate_y = np.array([])  # y pos of evolving organisms
        new_x = np.array([])  # x pos of new organisms
        new_y = np.array([])  # y pos of new organisms
        s_new = np.array([])  # speeds of new organisms
        c_new = np.array([])  # consumption of new organisms
        e_new = np.array([])  # energy of new organisms
        s = np.array([])      # speeds of remaining organisms
        c = np.array([])      # consumption of remaining organisms
        e = np.array([])      # energy of remaining organisms
        for j in range(len(active[0])):
            exited = False
            for speed in range(1, int(speeds[j]) + 1):
                next_x = active[0][j]
                next_y = active[1][j]
                while True:
                    if (not avaialble(next_x, next_y, grid)):
                        break

                    choice = np.random.rand()
                    if (choice < 0.5):
                        next_x, next_y = closest(next_x, next_y, active_food, grid)
                    else:
                        choice = np.random.rand()    
                        if (choice < 0.25): # Left
                            next_x -= 1
                        elif (choice < 0.5): # Right
                            next_x += 1
                        elif (choice < 0.75): # Up
                            next_y += 1
                        else:                # Down
                            next_y -= 1    


                   #next_x, next_y = closest(next_x, next_y, active_food, grid) # alternate

                    # Boundary Checks
                    if next_x < 1:
                        next_x = 1
                    if next_x >= n - 1:
                        next_x = n - 2
                    if next_y < 1:
                        next_y = 1
                    if next_y >= n - 1:
                        next_y = n - 2

                    # Check if theres already an organism there
                    if (grid[int(next_y), int(next_x)] != 1):
                        break

                grid[int(active[1][j]), int(active[0][j])] = 0 # Old location
                active[0][j] = next_x
                active[1][j] = next_y
                if (grid[int(next_y), int(next_x)] != -1 and speed == speeds[j]):              # Found no food
                    exited = True
                    if (energy[j] > 1):
                        curr_x = np.append(curr_x, next_x)
                        curr_y = np.append(curr_y, next_y)
                        s = np.append(s, speeds[j])
                        c = np.append(c, consumption[j])
                        e = np.append(e, energy[j] - 1)
                        grid[int(next_y), int(next_x)] = 1 # New location
                    break
                elif grid[int(next_y), int(next_x)] == -1 and consumption[j] + 1 == 2: # Found food + evolve
                    print("Duplicate")
                    exited = True
                    ate_x = np.append(ate_x, next_x)
                    ate_y = np.append(ate_y, next_y)

                    # Create 2 new children
                    new_x = np.append(new_x, next_x)
                    new_y = np.append(new_y, next_y)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        s_new = np.append(s_new, speeds[j] + 1 if speeds[j] < 4 else 4)
                    elif prob < 0.66:
                        s_new = np.append(s_new, speeds[j] - 1 if speeds[j] > 1 else 1)
                    else:
                        s_new = np.append(s_new, speeds[j])
                    c_new = np.append(c_new, 0)
                    e_new = np.append(e_new, 15)
                    
                    new_x = np.append(new_x, next_x)
                    new_y = np.append(new_y, next_y)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        s_new = np.append(s_new, speeds[j] + 1 if speeds[j] < 4 else 4)
                    elif prob < 0.66:
                        s_new = np.append(s_new, speeds[j] - 1 if speeds[j] > 1 else 1)
                    else:
                        s_new = np.append(s_new, speeds[j])
                    c_new = np.append(c_new, 0)
                    e_new = np.append(e_new, 15)
                    grid[int(next_y), int(next_x)] = 1 # New location
                    break
                elif grid[int(next_y), int(next_x)] == -1 and consumption[j] + 1 < 2: # Found food, no evolution
                    exited = True
                    curr_x = np.append(curr_x, next_x)
                    curr_y = np.append(curr_y, next_y)
                    s = np.append(s, speeds[j])
                    c = np.append(c, consumption[j] + 1)
                    e = np.append(e, energy[j] + 15)
                    grid[int(next_y), int(next_x)] = 1 # New location
                    break
                grid[int(next_y), int(next_x)] = 1 # New location
                
            energy[j] -= 1    
            if (exited != True):
                print("How is this possible")
                
        rem_food_x = np.array([])
        rem_food_y = np.array([])
        
        for j in range(len(active_food[0])):
            if (grid[int(active_food[1, j]), int(active_food[0, j])] == -1):
                rem_food_x = np.append(rem_food_x, active_food[0, j])
                rem_food_y = np.append(rem_food_y, active_food[1, j])
        possible_food = spaces_left(grid, 2, n - 2)
        f = 0
        need = food_count - len(rem_food_x)
        while f < possible_food and f < need:                           # Regenerate food
            new_food = np.round(np.random.rand(2) * (n - 4)) + 2
            if (grid[int(new_food[1]), int(new_food[0])] == 0):
                rem_food_x = np.append(rem_food_x, new_food[0])
                rem_food_y = np.append(rem_food_y, new_food[1])
                grid[int(new_food[1]), int(new_food[0])] = -1
                f += 1
        
        speed1_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 1])
        speed1_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 1])
        speed2_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 2])
        speed2_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 2])
        speed3_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 3])
        speed3_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 3])
        speed4_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 4])
        speed4_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 4])

        active_food = np.array([rem_food_x, rem_food_y])
        active = np.array([curr_x, curr_y])
        consumption = np.append(c, c_new)
        speeds = np.append(s, s_new)
        energy = np.append(e, e_new)
        axis[0].clear()
        axis[0].set_xlim(0, n)
        axis[0].set_ylim(0, n)
        
        axis[0].scatter(ate_x, ate_y, c="green")
        
        for x0, y0 in zip(rem_food_x, rem_food_y):
            ab = AnnotationBbox(getImage(paths[0]), (x0, y0), frameon=False)
            axis[0].add_artist(ab)
        
        #axis[0].scatter(rem_food_x, rem_food_y, c="red", marker="+", label="Food")
        axis[0].scatter(speed1_x, speed1_y, c="blue", label="Speed 1", s=80)
        axis[0].scatter(speed2_x, speed2_y, c="orange", label="Speed 2", s=80)
        axis[0].scatter(speed3_x, speed3_y, c="gray", label="Speed 3", s=80)
        axis[0].scatter(speed4_x, speed4_y, c="brown", label="Speed 4", s=80)
        
        
        
        axis[0].set_title("Natural Selection Sim")

        # Put a legend below current axis
        axis[0].legend(loc='center left', bbox_to_anchor=(1, 0.5))
        '''
        axis[1].clear()
        axis[1].set_title("Speed distribution")
        bar_colors = ['tab:blue','tab:orange', 'tab:gray', 'tab:brown']
        labels = ["Speed " + str(k) for k in range(1, 5)]
        heights = [len(speed1_x), len(speed2_x), len(speed3_x), len(speed4_x)]
        axis[1].bar(labels, heights, color=bar_colors)
        '''
        axis[1].set_title("Speed distribution")
        axis[1].bar(i, len(speed1_x), color="tab:blue", label="Speed 1")
        axis[1].bar(i, len(speed2_x), color="tab:orange", label="Speed 2", bottom=len(speed1_x))
        axis[1].bar(i, len(speed3_x), color="tab:gray", label="Speed 3", bottom=(len(speed1_x) + len(speed2_x)))
        axis[1].bar(i, len(speed4_x), color="tab:brown", label="Speed 4", 
                   bottom=(len(speed1_x) + len(speed2_x) + len(speed3_x)))
        axis[1].set_xlim(0, iterations)
        if i == 0:
            axis[1].legend(loc='upper center', bbox_to_anchor=(0.5, -0.05),
                           fancybox=True, shadow=True, ncol=5)
        
        plt.show()
        plt.draw()
        plt.pause(0.1)
        writer.grab_frame()
        print("Curr:", len(curr_x))
        active = np.array([np.append(curr_x, new_x), np.append(curr_y, new_y)])
        print("New total:", len(active[0]))
    print(len(active[0]))

Curr: 30
New total: 30
Curr: 30
New total: 30
Curr: 30
New total: 30
Curr: 30
New total: 30
Curr: 30
New total: 30
Duplicate
Curr: 29
New total: 31
Curr: 31
New total: 31
Curr: 31
New total: 31
Curr: 31
New total: 31
Curr: 31
New total: 31
Curr: 31
New total: 31
Curr: 31
New total: 31
Curr: 31
New total: 31
Curr: 31
New total: 31
Duplicate
Curr: 10
New total: 12
Duplicate
Curr: 11
New total: 13
Duplicate
Curr: 12
New total: 14
Curr: 14
New total: 14
Duplicate
Curr: 13
New total: 15
Duplicate
Curr: 14
New total: 16
Duplicate
Curr: 15
New total: 17
Duplicate
Duplicate
Curr: 15
New total: 19
Curr: 19
New total: 19
Curr: 19
New total: 19
Duplicate
Curr: 18
New total: 20
Duplicate
Curr: 19
New total: 21
Curr: 21
New total: 21
Curr: 21
New total: 21
Curr: 21
New total: 21
Duplicate
Duplicate
Curr: 19
New total: 23
Duplicate
Curr: 20
New total: 22
Curr: 21
New total: 21
Duplicate
Curr: 20
New total: 22
Curr: 22
New total: 22
Duplicate
Duplicate
Duplicate
Curr: 18
New total: 24
Curr: 23
New to

# Speed and Sizes

In [334]:
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Final', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=4, metadata=metadata,bitrate=200000)
fig, axis = plt.subplots(1, 3, figsize=(15.4,4.4))
box = axis[0].get_position()
axis[0].set_position([box.x0, box.y0, box.width * 0.8, box.height])

box = axis[1].get_position()
axis[1].set_position([box.x0, box.y0, box.width * 0.8, box.height])

box = axis[2].get_position()
axis[2].set_position([box.x0, box.y0, box.width * 0.8, box.height])


paths = ['nugget.jpg']

n = 30
food_count = 15
initial_energy = 10
grid, food_loc, org_loc = init(n, food_count)

with writer.saving(fig, "animation2.mp4", dpi=200):
    iterations = 70
    active = np.copy(org_loc)
    active_food = np.copy(food_loc)
    sizes = np.ones(len(active[0]))        # current sizes
    speeds = np.ones(len(active[0]))       # current speeds
    consumption = np.zeros(len(active[0])) # current consumption
    energy = np.ones(len(active[0])) * initial_energy
    for i in range(iterations):
        curr_x = np.array([])  # x pos of current organisms
        curr_y = np.array([])  # y pos of current organisms
        ate_x = np.array([])   # x pos of evolving organisms
        ate_y = np.array([])   # y pos of evolving organisms
        new_x = np.array([])   # x pos of new organisms
        new_y = np.array([])   # y pos of new organisms
        s_new = np.array([])   # speeds of new organisms
        c_new = np.array([])   # consumption of new organisms
        e_new = np.array([])   # energy of new organisms
        size_new = np.array([])# sizes of new organisms 
        s = np.array([])       # speeds of remaining organisms
        c = np.array([])       # consumption of remaining organisms
        e = np.array([])       # energy of remaining organisms
        size = np.array([])    # sizes of remaining organisms
        for j in range(len(active[0])):
            exited = False
            for speed in range(1, int(speeds[j]) + 1):
                next_x = active[0][j]
                next_y = active[1][j]
                while True:
                    if (not avaialble(next_x, next_y, grid)):
                        break

                    choice = np.random.rand()
                    if (choice < 0.75):
                        next_x, next_y = closest(next_x, next_y, active_food, grid)
                    else:
                        choice = np.random.rand()    
                        if (choice < 0.25): # Left
                            next_x -= 1
                        elif (choice < 0.5): # Right
                            next_x += 1
                        elif (choice < 0.75): # Up
                            next_y += 1
                        else:                # Down
                            next_y -= 1    


                   #next_x, next_y = closest(next_x, next_y, active_food, grid) # alternate

                    # Boundary Checks
                    if next_x < 1:
                        next_x = 1
                    if next_x >= n - 1:
                        next_x = n - 2
                    if next_y < 1:
                        next_y = 1
                    if next_y >= n - 1:
                        next_y = n - 2

                    # Check if theres already an organism there
                    if (grid[int(next_y), int(next_x)] <= sizes[j] * 1/2):
                        break

                grid[int(active[1][j]), int(active[0][j])] = 0 # Old location
                active[0][j] = next_x
                active[1][j] = next_y
                if (grid[int(next_y), int(next_x)] != -1 and speed == speeds[j]):              # Found no food
                    exited = True
                    if (energy[j] > 1):
                        curr_x = np.append(curr_x, next_x)
                        curr_y = np.append(curr_y, next_y)
                        s = np.append(s, speeds[j])
                        c = np.append(c, consumption[j])
                        e = np.append(e, energy[j] - 1)
                        size = np.append(size, sizes[j])
                        grid[int(next_y), int(next_x)] = 1 # New location
                    break
                elif grid[int(next_y), int(next_x)] == -1 and consumption[j] + 1 == 2*sizes[j]: # Found food + evolve
                    print("Duplicate")
                    exited = True
                    ate_x = np.append(ate_x, next_x)
                    ate_y = np.append(ate_y, next_y)

                    # Create 2 new children
                    new_x = np.append(new_x, next_x)
                    new_y = np.append(new_y, next_y)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        s_new = np.append(s_new, speeds[j] + 1 if speeds[j] < 4 else 4)
                    elif prob < 0.66:
                        s_new = np.append(s_new, speeds[j] - 1 if speeds[j] > 1 else 1)
                    else:
                        s_new = np.append(s_new, speeds[j])
                    c_new = np.append(c_new, 0)
                    e_new = np.append(e_new, initial_energy)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        size_new = np.append(size_new, sizes[j] + 1 if sizes[j] < 4 else 4)
                    elif prob < 0.66:
                        size_new = np.append(size_new, sizes[j] - 1 if sizes[j] > 1 else 1)
                    else:
                        size_new = np.append(size_new, sizes[j])
                    
                    new_x = np.append(new_x, next_x)
                    new_y = np.append(new_y, next_y)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        s_new = np.append(s_new, speeds[j] + 1 if speeds[j] < 4 else 4)
                    elif prob < 0.66:
                        s_new = np.append(s_new, speeds[j] - 1 if speeds[j] > 1 else 1)
                    else:
                        s_new = np.append(s_new, speeds[j])
                    c_new = np.append(c_new, 0)
                    e_new = np.append(e_new, initial_energy)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        size_new = np.append(size_new, sizes[j] + 1 if sizes[j] < 4 else 4)
                    elif prob < 0.66:
                        size_new = np.append(size_new, sizes[j] - 1 if sizes[j] > 1 else 1)
                    else:
                        size_new = np.append(size_new, sizes[j])
                    
                    grid[int(next_y), int(next_x)] = 1 # New location
                    break
                elif grid[int(next_y), int(next_x)] == -1 and consumption[j]+1 < 2*sizes[j]: # Found food, no evolution
                    exited = True
                    curr_x = np.append(curr_x, next_x)
                    curr_y = np.append(curr_y, next_y)
                    s = np.append(s, speeds[j])
                    c = np.append(c, consumption[j] + 1)
                    e = np.append(e, energy[j] + initial_energy)
                    size = np.append(size, sizes[j])
                    grid[int(next_y), int(next_x)] = 1 # New location
                    break
                grid[int(next_y), int(next_x)] = 1 # New location
                
            energy[j] -= sizes[j]    
            if (exited != True):
                print("How is this possible")
                
        rem_food_x = np.array([])
        rem_food_y = np.array([])
        
        for j in range(len(active_food[0])):
            if (grid[int(active_food[1, j]), int(active_food[0, j])] == -1):
                rem_food_x = np.append(rem_food_x, active_food[0, j])
                rem_food_y = np.append(rem_food_y, active_food[1, j])
        possible_food = spaces_left(grid, 2, n - 2)
        f = 0
        need = food_count - len(rem_food_x)
        while f < possible_food and f < need:                           # Regenerate food
            new_food = np.round(np.random.rand(2) * (n - 4)) + 2
            if (grid[int(new_food[1]), int(new_food[0])] == 0):
                rem_food_x = np.append(rem_food_x, new_food[0])
                rem_food_y = np.append(rem_food_y, new_food[1])
                grid[int(new_food[1]), int(new_food[0])] = -1
                f += 1
        
        speed1_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 1])
        speed1_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 1])
        speed1_sizes = (np.array([size[k] for k in range(len(size)) if s[k] == 1]) / 2) + 1
        
        speed2_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 2])
        speed2_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 2])
        speed2_sizes = (np.array([size[k] for k in range(len(size)) if s[k] == 2]) / 2) + 1
        
        speed3_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 3])
        speed3_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 3])
        speed3_sizes = (np.array([size[k] for k in range(len(size)) if s[k] == 3]) / 2) + 1
        
        speed4_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 4])
        speed4_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 4])
        speed4_sizes = (np.array([size[k] for k in range(len(size)) if s[k] == 4]) / 2) + 1
        
        size1 = np.count_nonzero(sizes == 1)
        size2 = np.count_nonzero(sizes == 2)
        size3 = np.count_nonzero(sizes == 3)
        size4 = np.count_nonzero(sizes == 4)

        active_food = np.array([rem_food_x, rem_food_y])
        active = np.array([curr_x, curr_y])
        consumption = np.append(c, c_new)
        speeds = np.append(s, s_new)
        energy = np.append(e, e_new)
        sizes = np.append(size, size_new)
        axis[1].clear()
        axis[1].set_xlim(0, n)
        axis[1].set_ylim(0, n)
        
        axis[1].scatter(ate_x, ate_y, c="green")
        
        for x0, y0 in zip(rem_food_x, rem_food_y):
            ab = AnnotationBbox(getImage(paths[0]), (x0, y0), frameon=False)
            axis[1].add_artist(ab)
        
        #axis[1].scatter(rem_food_x, rem_food_y, c="red", marker="+", label="Food")
        axis[1].scatter(speed1_x, speed1_y, c="blue", label="Speed 1", s=(80 * speed1_sizes))
        axis[1].scatter(speed2_x, speed2_y, c="orange", label="Speed 2", s=(80 * speed2_sizes))
        axis[1].scatter(speed3_x, speed3_y, c="gray", label="Speed 3", s=(80 * speed3_sizes))
        axis[1].scatter(speed4_x, speed4_y, c="brown", label="Speed 4", s=(80 * speed4_sizes))
        
        
        axis[1].set_title("Natural Selection Sim")

        # Put a legend below current axis
        axis[1].legend(loc='center left', bbox_to_anchor=(1, 0.5))
        
        '''
        axis[1].clear()
        axis[1].set_title("Speed distribution")
        bar_colors = ['tab:blue','tab:orange', 'tab:gray', 'tab:brown']
        labels = ["Speed " + str(k) for k in range(1, 5)]
        heights = [len(speed1_x), len(speed2_x), len(speed3_x), len(speed4_x)]
        axis[1].bar(labels, heights, color=bar_colors)
        '''
        axis[2].set_title("Speed distribution")
        axis[2].bar(i, len(speed1_x), color="tab:blue", label="Speed 1")
        axis[2].bar(i, len(speed2_x), color="tab:orange", label="Speed 2", bottom=len(speed1_x))
        axis[2].bar(i, len(speed3_x), color="tab:gray", label="Speed 3", bottom=(len(speed1_x) + len(speed2_x)))
        axis[2].bar(i, len(speed4_x), color="tab:brown", label="Speed 4", 
                   bottom=(len(speed1_x) + len(speed2_x) + len(speed3_x)))
        axis[2].set_xlim(0, iterations)
        if i == 0:
            axis[2].legend(loc='center left', bbox_to_anchor=(1, 0.5))
        
        '''
        axis[2].clear()
        axis[2].set_title("Size distribution")
        axis[2].hist(sizes)
        '''
        
        axis[0].set_title("Size distribution")
        axis[0].bar(i, size1, color="tab:blue", label="Size 1")
        axis[0].bar(i, size2, color="tab:orange", label="Size 2", bottom=size1)
        axis[0].bar(i, size3, color="tab:gray", label="Size 3", bottom=(size1 + size2))
        axis[0].bar(i, size4, color="tab:brown", label="Size 4", 
                   bottom=(size1 + size2 + size3))
        axis[0].set_xlim(0, iterations)
        if i == 0:
            axis[0].legend(loc='center left', bbox_to_anchor=(1, 0.5))
        
        plt.show()
        plt.draw()
        plt.pause(0.1)
        writer.grab_frame()
        print("Curr:", len(curr_x))
        active = np.array([np.append(curr_x, new_x), np.append(curr_y, new_y)])
        print("New total:", len(active[0]))
    print(len(active[0]))

Curr: 30
New total: 30
Curr: 30
New total: 30
Curr: 30
New total: 30
Curr: 30
New total: 30
Duplicate
Curr: 29
New total: 31
Curr: 31
New total: 31
Curr: 31
New total: 31
Duplicate
Curr: 30
New total: 32
Curr: 32
New total: 32
Duplicate
Curr: 12
New total: 14
Duplicate
Curr: 13
New total: 15
Curr: 15
New total: 15
Duplicate
Duplicate
Curr: 13
New total: 17
Duplicate
Duplicate
Curr: 15
New total: 19
Curr: 18
New total: 18
Duplicate
Curr: 17
New total: 19
Curr: 19
New total: 19
Curr: 18
New total: 18
Duplicate
Duplicate
Duplicate
Curr: 15
New total: 21
Curr: 20
New total: 20
Duplicate
Duplicate
Curr: 16
New total: 20
Duplicate
Curr: 19
New total: 21
Duplicate
Curr: 18
New total: 20
Curr: 18
New total: 18
Curr: 18
New total: 18
Duplicate
Curr: 15
New total: 17
Curr: 17
New total: 17
Duplicate
Curr: 16
New total: 18
Duplicate
Curr: 17
New total: 19
Curr: 19
New total: 19
Curr: 19
New total: 19
Duplicate
Curr: 17
New total: 19
Duplicate
Curr: 17
New total: 19
Duplicate
Duplicate
Curr: 17
Ne

# Animation 3

In [331]:
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Final', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=4, metadata=metadata,bitrate=200000)
fig, axis = plt.subplots(1, 2, figsize=(12.4,6.4))
box = axis[0].get_position()
axis[0].set_position([box.x0, box.y0, box.width * 0.8, box.height])

box = axis[1].get_position()
axis[1].set_position([box.x0, box.y0 + box.height * 0.1,
                 box.width, box.height * 0.9])

paths = ['nugget.jpg']

n = 30
food_count = 15
grid, food_loc, org_loc = init(n, food_count)
#org_loc = np.array([[org_loc[0][0]],[org_loc[1][0]]])

with writer.saving(fig, "animation3.mp4", dpi=200):
    iterations = 80
    active = np.copy(org_loc)
    active_food = np.copy(food_loc)
    sizes = np.ones(len(active[0]))        # current sizes
    speeds = np.ones(len(active[0]))       # current speeds
    consumption = np.zeros(len(active[0])) # current consumption
    energy = np.ones(len(active[0])) * 15
    for i in range(iterations):
        curr_x = np.array([]) # x pos of current organisms
        curr_y = np.array([]) # y pos of current organisms
        ate_x = np.array([])  # x pos of evolving organisms
        ate_y = np.array([])  # y pos of evolving organisms
        new_x = np.array([])  # x pos of new organisms
        new_y = np.array([])  # y pos of new organisms
        s_new = np.array([])  # speeds of new organisms
        c_new = np.array([])  # consumption of new organisms
        e_new = np.array([])  # energy of new organisms
        s = np.array([])      # speeds of remaining organisms
        c = np.array([])      # consumption of remaining organisms
        e = np.array([])      # energy of remaining organisms
        for j in range(len(active[0])):
            exited = False
            for speed in range(1, int(speeds[j]) + 1):
                next_x = active[0][j]
                next_y = active[1][j]
                while True:
                    if (not avaialble(next_x, next_y, grid)):
                        break

                    choice = np.random.rand()
                    if (choice < 0.75):
                        next_x, next_y = closest(next_x, next_y, active_food, grid)
                    else:
                        choice = np.random.rand()    
                        if (choice < 0.25): # Left
                            next_x -= 1
                        elif (choice < 0.5): # Right
                            next_x += 1
                        elif (choice < 0.75): # Up
                            next_y += 1
                        else:                # Down
                            next_y -= 1    


                   #next_x, next_y = closest(next_x, next_y, active_food, grid) # alternate

                    # Boundary Checks
                    if next_x < 1:
                        next_x = 1
                    if next_x >= n - 1:
                        next_x = n - 2
                    if next_y < 1:
                        next_y = 1
                    if next_y >= n - 1:
                        next_y = n - 2

                    # Check if theres already an organism there
                    if (grid[int(next_y), int(next_x)] != 1):
                        break

                grid[int(active[1][j]), int(active[0][j])] = 0 # Old location
                active[0][j] = next_x
                active[1][j] = next_y
                if (grid[int(next_y), int(next_x)] != -1 and speed == speeds[j]):              # Found no food
                    exited = True
                    if (energy[j] > 1):
                        curr_x = np.append(curr_x, next_x)
                        curr_y = np.append(curr_y, next_y)
                        s = np.append(s, speeds[j])
                        c = np.append(c, consumption[j])
                        e = np.append(e, energy[j] - 1)
                        grid[int(next_y), int(next_x)] = 1 # New location
                    break
                elif grid[int(next_y), int(next_x)] == -1 and consumption[j] + 1 == 2: # Found food + evolve
                    print("Duplicate")
                    exited = True
                    ate_x = np.append(ate_x, next_x)
                    ate_y = np.append(ate_y, next_y)

                    # Create 2 new children
                    new_x = np.append(new_x, next_x)
                    new_y = np.append(new_y, next_y)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        s_new = np.append(s_new, speeds[j] + 1 if speeds[j] < 4 else 4)
                    elif prob < 0.66:
                        s_new = np.append(s_new, speeds[j] - 1 if speeds[j] > 1 else 1)
                    else:
                        s_new = np.append(s_new, speeds[j])
                    c_new = np.append(c_new, 0)
                    e_new = np.append(e_new, 15)
                    
                    new_x = np.append(new_x, next_x)
                    new_y = np.append(new_y, next_y)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        s_new = np.append(s_new, speeds[j] + 1 if speeds[j] < 4 else 4)
                    elif prob < 0.66:
                        s_new = np.append(s_new, speeds[j] - 1 if speeds[j] > 1 else 1)
                    else:
                        s_new = np.append(s_new, speeds[j])
                    c_new = np.append(c_new, 0)
                    e_new = np.append(e_new, 15)
                    grid[int(next_y), int(next_x)] = 1 # New location
                    break
                elif grid[int(next_y), int(next_x)] == -1 and consumption[j] + 1 < 2: # Found food, no evolution
                    exited = True
                    curr_x = np.append(curr_x, next_x)
                    curr_y = np.append(curr_y, next_y)
                    s = np.append(s, speeds[j])
                    c = np.append(c, consumption[j] + 1)
                    e = np.append(e, energy[j] + 15)
                    grid[int(next_y), int(next_x)] = 1 # New location
                    break
                grid[int(next_y), int(next_x)] = 1 # New location
                
            energy[j] -= 1    
            if (exited != True):
                print("How is this possible")
                
        rem_food_x = np.array([])
        rem_food_y = np.array([])
        
        for j in range(len(active_food[0])):
            if (grid[int(active_food[1, j]), int(active_food[0, j])] == -1):
                rem_food_x = np.append(rem_food_x, active_food[0, j])
                rem_food_y = np.append(rem_food_y, active_food[1, j])
        possible_food = spaces_left(grid, 2, n - 2)
        f = 0
        need = food_count - len(rem_food_x)
        while f < possible_food and f < need:                           # Regenerate food
            new_food = np.round(np.random.rand(2) * (n - 4)) + 2
            if (grid[int(new_food[1]), int(new_food[0])] == 0):
                rem_food_x = np.append(rem_food_x, new_food[0])
                rem_food_y = np.append(rem_food_y, new_food[1])
                grid[int(new_food[1]), int(new_food[0])] = -1
                f += 1
        
        speed1_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 1])
        speed1_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 1])
        speed2_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 2])
        speed2_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 2])
        speed3_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 3])
        speed3_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 3])
        speed4_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 4])
        speed4_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 4])

        active_food = np.array([rem_food_x, rem_food_y])
        active = np.array([curr_x, curr_y])
        consumption = np.append(c, c_new)
        speeds = np.append(s, s_new)
        energy = np.append(e, e_new)
        axis[0].clear()
        axis[0].set_xlim(0, n)
        axis[0].set_ylim(0, n)
        
        axis[0].scatter(ate_x, ate_y, c="green")
        
        for x0, y0 in zip(rem_food_x, rem_food_y):
            ab = AnnotationBbox(getImage(paths[0]), (x0, y0), frameon=False)
            axis[0].add_artist(ab)
        
        #axis[0].scatter(rem_food_x, rem_food_y, c="red", marker="+", label="Food")
        axis[0].scatter(speed1_x, speed1_y, c="blue", label="Speed 1", s=80)
        axis[0].scatter(speed2_x, speed2_y, c="orange", label="Speed 2", s=80)
        axis[0].scatter(speed3_x, speed3_y, c="gray", label="Speed 3", s=80)
        axis[0].scatter(speed4_x, speed4_y, c="brown", label="Speed 4", s=80)
        
        axis[0].set_title("Natural Selection Sim")

        # Put a legend below current axis
        axis[0].legend(loc='center left', bbox_to_anchor=(1, 0.5))
        '''
        axis[1].clear()
        axis[1].set_title("Speed distribution")
        bar_colors = ['tab:blue','tab:orange', 'tab:gray', 'tab:brown']
        labels = ["Speed " + str(k) for k in range(1, 5)]
        heights = [len(speed1_x), len(speed2_x), len(speed3_x), len(speed4_x)]
        axis[1].bar(labels, heights, color=bar_colors)
        '''
        axis[1].set_title("Speed distribution")
        axis[1].bar(i, len(speed1_x), color="tab:blue", label="Speed 1")
        axis[1].bar(i, len(speed2_x), color="tab:orange", label="Speed 2", bottom=len(speed1_x))
        axis[1].bar(i, len(speed3_x), color="tab:gray", label="Speed 3", bottom=(len(speed1_x) + len(speed2_x)))
        axis[1].bar(i, len(speed4_x), color="tab:brown", label="Speed 4", 
                   bottom=(len(speed1_x) + len(speed2_x) + len(speed3_x)))
        axis[1].set_xlim(0, iterations)
        if i == 0:
            axis[1].legend(loc='upper center', bbox_to_anchor=(0.5, -0.05),
                           fancybox=True, shadow=True, ncol=5)
        
        plt.show()
        plt.draw()
        plt.pause(0.1)
        writer.grab_frame()
        print("Curr:", len(curr_x))
        active = np.array([np.append(curr_x, new_x), np.append(curr_y, new_y)])
        print("New total:", len(active[0]))
    print(len(active[0]))

Curr: 30
New total: 30
Curr: 30
New total: 30
Curr: 30
New total: 30
Curr: 30
New total: 30
Curr: 30
New total: 30
Duplicate
Curr: 29
New total: 31
Duplicate
Curr: 30
New total: 32
Curr: 32
New total: 32
Duplicate
Curr: 31
New total: 33
Duplicate
Duplicate
Curr: 31
New total: 35
Curr: 35
New total: 35
Duplicate
Duplicate
Curr: 33
New total: 37
Duplicate
Curr: 36
New total: 38
Duplicate
Curr: 37
New total: 39
Duplicate
Curr: 26
New total: 28
Duplicate
Duplicate
Duplicate
Curr: 25
New total: 31
Duplicate
Duplicate
Curr: 29
New total: 33
Duplicate
Curr: 32
New total: 34
Curr: 34
New total: 34
Duplicate
Duplicate
Duplicate
Curr: 31
New total: 37
Duplicate
Duplicate
Duplicate
Duplicate
Duplicate
Curr: 32
New total: 42
Duplicate
Curr: 40
New total: 42
Duplicate
Curr: 41
New total: 43
Duplicate
Duplicate
Duplicate
Duplicate
Curr: 39
New total: 47
Duplicate
Duplicate
Curr: 43
New total: 47
Duplicate
Duplicate
Duplicate
Curr: 44
New total: 50
Duplicate
Duplicate
Curr: 46
New total: 50
Duplicate

# Animation 4: One organism

In [337]:
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Final', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=4, metadata=metadata,bitrate=200000)
fig, axis = plt.subplots(1, 3, figsize=(15.4,4.4))
box = axis[0].get_position()
axis[0].set_position([box.x0, box.y0, box.width * 0.8, box.height])

box = axis[1].get_position()
axis[1].set_position([box.x0, box.y0, box.width * 0.8, box.height])

box = axis[2].get_position()
axis[2].set_position([box.x0, box.y0, box.width * 0.8, box.height])


paths = ['nugget.jpg']

n = 30
food_count = 15
initial_energy = 10
grid, food_loc, org_loc = init(n, food_count)
org_loc = np.array([[org_loc[0][0]],[org_loc[1][0]]])

with writer.saving(fig, "animation4.mp4", dpi=200):
    iterations = 70
    active = np.copy(org_loc)
    active_food = np.copy(food_loc)
    sizes = np.ones(len(active[0]))        # current sizes
    speeds = np.ones(len(active[0]))       # current speeds
    consumption = np.zeros(len(active[0])) # current consumption
    energy = np.ones(len(active[0])) * initial_energy
    for i in range(iterations):
        curr_x = np.array([])  # x pos of current organisms
        curr_y = np.array([])  # y pos of current organisms
        ate_x = np.array([])   # x pos of evolving organisms
        ate_y = np.array([])   # y pos of evolving organisms
        new_x = np.array([])   # x pos of new organisms
        new_y = np.array([])   # y pos of new organisms
        s_new = np.array([])   # speeds of new organisms
        c_new = np.array([])   # consumption of new organisms
        e_new = np.array([])   # energy of new organisms
        size_new = np.array([])# sizes of new organisms 
        s = np.array([])       # speeds of remaining organisms
        c = np.array([])       # consumption of remaining organisms
        e = np.array([])       # energy of remaining organisms
        size = np.array([])    # sizes of remaining organisms
        for j in range(len(active[0])):
            exited = False
            for speed in range(1, int(speeds[j]) + 1):
                next_x = active[0][j]
                next_y = active[1][j]
                while True:
                    if (not avaialble(next_x, next_y, grid)):
                        break

                    choice = np.random.rand()
                    if (choice < 0.7):
                        next_x, next_y = closest(next_x, next_y, active_food, grid)
                    else:
                        choice = np.random.rand()    
                        if (choice < 0.25): # Left
                            next_x -= 1
                        elif (choice < 0.5): # Right
                            next_x += 1
                        elif (choice < 0.75): # Up
                            next_y += 1
                        else:                # Down
                            next_y -= 1    


                   #next_x, next_y = closest(next_x, next_y, active_food, grid) # alternate

                    # Boundary Checks
                    if next_x < 1:
                        next_x = 1
                    if next_x >= n - 1:
                        next_x = n - 2
                    if next_y < 1:
                        next_y = 1
                    if next_y >= n - 1:
                        next_y = n - 2

                    # Check if theres already an organism there
                    if (grid[int(next_y), int(next_x)] <= sizes[j] * 1/2):
                        break

                grid[int(active[1][j]), int(active[0][j])] = 0 # Old location
                active[0][j] = next_x
                active[1][j] = next_y
                if (grid[int(next_y), int(next_x)] != -1 and speed == speeds[j]):              # Found no food
                    exited = True
                    if (energy[j] > 1):
                        curr_x = np.append(curr_x, next_x)
                        curr_y = np.append(curr_y, next_y)
                        s = np.append(s, speeds[j])
                        c = np.append(c, consumption[j])
                        e = np.append(e, energy[j] - 1)
                        size = np.append(size, sizes[j])
                        grid[int(next_y), int(next_x)] = 1 # New location
                    break
                elif grid[int(next_y), int(next_x)] == -1 and consumption[j] + 1 == 2*sizes[j]: # Found food + evolve
                    print("Duplicate")
                    exited = True
                    ate_x = np.append(ate_x, next_x)
                    ate_y = np.append(ate_y, next_y)

                    # Create 2 new children
                    new_x = np.append(new_x, next_x)
                    new_y = np.append(new_y, next_y)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        s_new = np.append(s_new, speeds[j] + 1 if speeds[j] < 4 else 4)
                    elif prob < 0.66:
                        s_new = np.append(s_new, speeds[j] - 1 if speeds[j] > 1 else 1)
                    else:
                        s_new = np.append(s_new, speeds[j])
                    c_new = np.append(c_new, 0)
                    e_new = np.append(e_new, initial_energy)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        size_new = np.append(size_new, sizes[j] + 1 if sizes[j] < 4 else 4)
                    elif prob < 0.66:
                        size_new = np.append(size_new, sizes[j] - 1 if sizes[j] > 1 else 1)
                    else:
                        size_new = np.append(size_new, sizes[j])
                    
                    new_x = np.append(new_x, next_x)
                    new_y = np.append(new_y, next_y)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        s_new = np.append(s_new, speeds[j] + 1 if speeds[j] < 4 else 4)
                    elif prob < 0.66:
                        s_new = np.append(s_new, speeds[j] - 1 if speeds[j] > 1 else 1)
                    else:
                        s_new = np.append(s_new, speeds[j])
                    c_new = np.append(c_new, 0)
                    e_new = np.append(e_new, initial_energy)
                    prob = np.random.rand()
                    if (prob < 0.33):
                        size_new = np.append(size_new, sizes[j] + 1 if sizes[j] < 4 else 4)
                    elif prob < 0.66:
                        size_new = np.append(size_new, sizes[j] - 1 if sizes[j] > 1 else 1)
                    else:
                        size_new = np.append(size_new, sizes[j])
                    
                    grid[int(next_y), int(next_x)] = 1 # New location
                    break
                elif grid[int(next_y), int(next_x)] == -1 and consumption[j]+1 < 2*sizes[j]: # Found food, no evolution
                    exited = True
                    curr_x = np.append(curr_x, next_x)
                    curr_y = np.append(curr_y, next_y)
                    s = np.append(s, speeds[j])
                    c = np.append(c, consumption[j] + 1)
                    e = np.append(e, energy[j] + initial_energy)
                    size = np.append(size, sizes[j])
                    grid[int(next_y), int(next_x)] = 1 # New location
                    break
                grid[int(next_y), int(next_x)] = 1 # New location
                
            energy[j] -= sizes[j]    
            if (exited != True):
                print("How is this possible")
                
        rem_food_x = np.array([])
        rem_food_y = np.array([])
        
        for j in range(len(active_food[0])):
            if (grid[int(active_food[1, j]), int(active_food[0, j])] == -1):
                rem_food_x = np.append(rem_food_x, active_food[0, j])
                rem_food_y = np.append(rem_food_y, active_food[1, j])
        possible_food = spaces_left(grid, 2, n - 2)
        f = 0
        need = food_count - len(rem_food_x)
        while f < possible_food and f < need:                           # Regenerate food
            new_food = np.round(np.random.rand(2) * (n - 4)) + 2
            if (grid[int(new_food[1]), int(new_food[0])] == 0):
                rem_food_x = np.append(rem_food_x, new_food[0])
                rem_food_y = np.append(rem_food_y, new_food[1])
                grid[int(new_food[1]), int(new_food[0])] = -1
                f += 1
        
        speed1_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 1])
        speed1_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 1])
        speed1_sizes = (np.array([size[k] for k in range(len(size)) if s[k] == 1]) / 2) + 1
        
        speed2_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 2])
        speed2_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 2])
        speed2_sizes = (np.array([size[k] for k in range(len(size)) if s[k] == 2]) / 2) + 1
        
        speed3_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 3])
        speed3_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 3])
        speed3_sizes = (np.array([size[k] for k in range(len(size)) if s[k] == 3]) / 2) + 1
        
        speed4_x = np.array([curr_x[k] for k in range(len(curr_x)) if s[k] == 4])
        speed4_y = np.array([curr_y[k] for k in range(len(curr_y)) if s[k] == 4])
        speed4_sizes = (np.array([size[k] for k in range(len(size)) if s[k] == 4]) / 2) + 1
        
        size1 = np.count_nonzero(sizes == 1)
        size2 = np.count_nonzero(sizes == 2)
        size3 = np.count_nonzero(sizes == 3)
        size4 = np.count_nonzero(sizes == 4)

        active_food = np.array([rem_food_x, rem_food_y])
        active = np.array([curr_x, curr_y])
        consumption = np.append(c, c_new)
        speeds = np.append(s, s_new)
        energy = np.append(e, e_new)
        sizes = np.append(size, size_new)
        axis[1].clear()
        axis[1].set_xlim(0, n)
        axis[1].set_ylim(0, n)
        
        axis[1].scatter(ate_x, ate_y, c="green")
        
        for x0, y0 in zip(rem_food_x, rem_food_y):
            ab = AnnotationBbox(getImage(paths[0]), (x0, y0), frameon=False)
            axis[1].add_artist(ab)
        
        #axis[1].scatter(rem_food_x, rem_food_y, c="red", marker="+", label="Food")
        axis[1].scatter(speed1_x, speed1_y, c="blue", label="Speed 1", s=(80 * speed1_sizes))
        axis[1].scatter(speed2_x, speed2_y, c="orange", label="Speed 2", s=(80 * speed2_sizes))
        axis[1].scatter(speed3_x, speed3_y, c="gray", label="Speed 3", s=(80 * speed3_sizes))
        axis[1].scatter(speed4_x, speed4_y, c="brown", label="Speed 4", s=(80 * speed4_sizes))
        
        axis[1].set_title("Natural Selection Sim")

        # Put a legend below current axis
        axis[1].legend(loc='center left', bbox_to_anchor=(1, 0.5))
        
        '''
        axis[1].clear()
        axis[1].set_title("Speed distribution")
        bar_colors = ['tab:blue','tab:orange', 'tab:gray', 'tab:brown']
        labels = ["Speed " + str(k) for k in range(1, 5)]
        heights = [len(speed1_x), len(speed2_x), len(speed3_x), len(speed4_x)]
        axis[1].bar(labels, heights, color=bar_colors)
        '''
        axis[2].set_title("Speed distribution")
        axis[2].bar(i, len(speed1_x), color="tab:blue", label="Speed 1")
        axis[2].bar(i, len(speed2_x), color="tab:orange", label="Speed 2", bottom=len(speed1_x))
        axis[2].bar(i, len(speed3_x), color="tab:gray", label="Speed 3", bottom=(len(speed1_x) + len(speed2_x)))
        axis[2].bar(i, len(speed4_x), color="tab:brown", label="Speed 4", 
                   bottom=(len(speed1_x) + len(speed2_x) + len(speed3_x)))
        axis[2].set_xlim(0, iterations)
        if i == 0:
            axis[2].legend(loc='center left', bbox_to_anchor=(1, 0.5))
        
        '''
        axis[2].clear()
        axis[2].set_title("Size distribution")
        axis[2].hist(sizes)
        '''
        
        axis[0].set_title("Size distribution")
        axis[0].bar(i, size1, color="tab:blue", label="Size 1")
        axis[0].bar(i, size2, color="tab:orange", label="Size 2", bottom=size1)
        axis[0].bar(i, size3, color="tab:gray", label="Size 3", bottom=(size1 + size2))
        axis[0].bar(i, size4, color="tab:brown", label="Size 4", 
                   bottom=(size1 + size2 + size3))
        axis[0].set_xlim(0, iterations)
        if i == 0:
            axis[0].legend(loc='center left', bbox_to_anchor=(1, 0.5))
        
        plt.show()
        plt.draw()
        plt.pause(0.1)
        writer.grab_frame()
        print("Curr:", len(curr_x))
        active = np.array([np.append(curr_x, new_x), np.append(curr_y, new_y)])
        print("New total:", len(active[0]))
    print(len(active[0]))

Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Curr: 1
New total: 1
Duplicate
Curr: 0
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Duplicate
Curr: 1
New total: 3
Curr: 3
New total: 3
Curr: 3
New total: 3
Curr: 2
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Curr: 2
New total: 2
Duplicate
Curr: 1
New total: 3
Curr: 3
New total: 3
Curr: 3
New total: 3
Curr: 3
New total: 3
Duplicate
Curr: 2
New total: 4
Duplicate
Curr: 3
New total: 5
Curr: 5
New total: 5
Curr: 5
New total: 5
Duplicate
Curr: 4
New total: 6
Duplicate
Curr: 5
New total: 7
Curr: 7
New total: 7
Curr: 